U ovoj sveci je napravljen ensamble modela kako bi se njihovim uprosecavanjem dobila predvidjena vrednost

In [2]:
import numpy as np
import pandas as pd
import keras
from sklearn import preprocessing
from sklearn import metrics
from tensorflow.keras.models import Sequential
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dense, SimpleRNN, RNN, LSTM, GRU, SpatialDropout1D, Dropout

In [3]:
import matplotlib.pyplot as plt
import os, os.path, sys
import copy

In [4]:
path = r"C:\Users\mata2\Desktop\master\Axis-projection-RNN\podaci\0k\X"

In [5]:
dir = os.listdir(path)

In [6]:
file_names = []
for file in dir:
    file_names.append(file)

Postoji 30 text fajlova, od kojih je 15 uzeto za treniranje, dok su preostalih 15 korisceni za testiranje

In [6]:
duzina = int(len(file_names)/2)

In [7]:
training_files = file_names[:duzina]
testing_files = file_names[-duzina:]

In [8]:
training_files_paths = []
testing_files_paths = []

for i in range(len(training_files)):
    training_files_paths.append(path+'\\'+training_files[i])
    testing_files_paths.append(path+'\\'+testing_files[i])

Napravljene su putanje za fajlove kako bi dinamicki napravili setove za treniranje i testiranje

In [9]:
training = {}
testing = {}

for i in range(len(training_files)):
    training['train_{}'.format(i)] = pd.read_csv(training_files_paths[i], header=None)[:61000].astype('int')
    testing['test_{}'.format(i)] = pd.read_csv(testing_files_paths[i], header=None)[:61000].astype('int')

Potencijalni time_stepovi su (1, 2, 4, 5, 8, 10, 20, 25, 40, 50, 61, 100), kako bi bili deljivi sa 61000

napravljeni su fajlovi sa min i max koordinatama iz svih fajlova za sve odbirke

In [7]:
min_kord = [float('inf') for x in range(61000)]
max_kord = [float('-inf') for x in range(61000)]

for file in file_names:
  current_file = pd.read_csv(path+'/'+file, header=None)[:61000].astype('int')

  for i in range(len(current_file)):
    if current_file[0][i] < min_kord[i]:
      min_kord[i] = current_file[0][i]
    elif current_file[0][i] > max_kord[i]:
      max_kord[i] = current_file[0][i]


best step = 20

In [11]:
def create_timeseries_split(data, time_steps):

  # Get the number of samples in the data
  num_samples = len(data) - time_steps

  # Create empty arrays to store features and target values
  x_train = np.zeros((num_samples, time_steps, 1))
  y_train = np.zeros((num_samples, 1))

  # Loop through the data and create features and target values
  for i in range(num_samples):
    # Extract a slice of data for the current feature
    x_train[i] = data[i:i+time_steps, :]

    # The target value is the next value after the feature
    y_train[i] = data[i+time_steps, 0]

  return x_train, y_train

In [12]:
time_steps = 5

In [13]:
train_X = {}
test_X = {}
train_y = {}
test_y = {}

for i in range(len(training_files)):
    train_X['train_X{}'.format(i)], train_y['train_y{}'.format(i)] = create_timeseries_split(np.asarray(training['train_{}'.format(i)]), time_steps)
    test_X['test_X{}'.format(i)], test_y['test_y{}'.format(i)] = create_timeseries_split(np.asarray(testing['test_{}'.format(i)]), time_steps)  

In [14]:
np.random.seed(1234)

In [15]:
input_shape = (time_steps,1)

best units:
    
units1 = [16,32]

units2 = [16,32]

units3 = [16,32]

units4 = [16,32]

units5 = [16,32]

best_skor:  238.99697875976562

best_unit1:  32

best_unit2:  16

best_unit3:  32

best_unit4:  32

best_unit5:  16

In [16]:
optimizer = keras.optimizers.Adam(learning_rate=0.00001)

napravljeno je 15 modela

In [17]:
for i in range(duzina):
    exec(f"model_{i} = Sequential([LSTM(units = 32, input_shape = input_shape, activation = keras.layers.LeakyReLU()), Dense(units = 16, activation=keras.layers.LeakyReLU()),Dense(units = 32, activation=keras.layers.LeakyReLU()),Dense(units = 32, activation=keras.layers.LeakyReLU()),Dense(units = 1, activation=keras.layers.LeakyReLU(), bias_initializer='zeros', kernel_initializer='normal')])")
    exec(f"model_{i}.compile(loss='mean_squared_error', optimizer = 'adam')")

In [20]:
for i in range(5):
#for i in range(duzina):
    exec(f"model_{i}.fit(train_X['train_X{i}'], train_y['train_y{i}'], epochs=10,batch_size = 64, verbose = 2)")

Epoch 1/10
954/954 - 3s - loss: 10090.9551 - 3s/epoch - 3ms/step
Epoch 2/10
954/954 - 3s - loss: 46219.8320 - 3s/epoch - 3ms/step
Epoch 3/10
954/954 - 3s - loss: 854788.9375 - 3s/epoch - 3ms/step
Epoch 4/10
954/954 - 3s - loss: 8080995.5000 - 3s/epoch - 3ms/step
Epoch 5/10
954/954 - 3s - loss: 2735579.7500 - 3s/epoch - 3ms/step
Epoch 6/10
954/954 - 3s - loss: 1139754.6250 - 3s/epoch - 3ms/step
Epoch 7/10
954/954 - 3s - loss: 171732.8281 - 3s/epoch - 3ms/step
Epoch 8/10
954/954 - 3s - loss: 10493.6318 - 3s/epoch - 3ms/step
Epoch 9/10
954/954 - 3s - loss: 10858.2295 - 3s/epoch - 3ms/step
Epoch 10/10
954/954 - 3s - loss: 14750.1484 - 3s/epoch - 3ms/step
Epoch 1/10
954/954 - 3s - loss: 9951407.0000 - 3s/epoch - 3ms/step
Epoch 2/10
954/954 - 3s - loss: 163787.5625 - 3s/epoch - 3ms/step
Epoch 3/10
954/954 - 3s - loss: 14755.4795 - 3s/epoch - 3ms/step
Epoch 4/10
954/954 - 3s - loss: 1079746.1250 - 3s/epoch - 3ms/step
Epoch 5/10
954/954 - 3s - loss: 10829761.0000 - 3s/epoch - 3ms/step
Epoch 6/

In [22]:
for i in range(5):
#for i in range(duzina):    
    exec(f"train_scores_{i} = model_{i}.evaluate(test_X['test_X{i}'], test_y['test_y{i}'])")

1907/1907 [==============================] - 4s 2ms/step - loss: 162264.4375


In [23]:
for i in range(5):
#for i in range(duzina):
    exec(f"train_predict_{i} = model_{i}.predict(train_X['train_X{i}'])")
    exec(f"test_predict_{i} = model_{i}.predict(test_X['test_X{i}'])")

1907/1907 [==============================] - 3s 2ms/step


In [222]:
n = 61000
test_size = len(testing_files)
avg_koord = [0 for x in range(n)]
for j in range(duzina):
    for i in range(n):
        exec(f"avg_koord[i] += testing['test_{j}'.format(j)][0][i]")
avg_kord = [x//duzina for x in avg_koord]

In [228]:
num_correct_train = 0
for i in range(len(train_predict_0)):
    if min_kord[i] <= train_predict_0[i][0] <= max_kord[i]:
        num_correct_train += 1
num_correct_train

7072

In [229]:
num_correct_test = 0
for i in range(len(test_predict_0)):
    if min_kord[i] <= test_predict_0[i][0] <= max_kord[i]:
        num_correct_test += 1
num_correct_test

7106

In [225]:
for i in range(len(test_predict_0)):
    if min_kord[i] <= test_predict_0[i][0] <= max_kord[i]:
        print(min_kord[i], test_predict_0[i][0], max_kord[i], 'index:', i)

-1 -0.43621117 0 index: 0
-1 -0.43621117 0 index: 1
14 30.893227 31 index: 6
26 33.171307 39 index: 9
29 36.70125 39 index: 10
34 41.247803 43 index: 11
40 49.578728 54 index: 12
45 64.3153 67 index: 13
82 107.06806 111 index: 17
91 112.810295 113 index: 18
237 246.70839 251 index: 27
241 254.82587 255 index: 28
9999 10020.986 10021 index: 312
9999 10012.36 10013 index: 313
9925 9948.714 9949 index: 4314
9906 9933.676 9939 index: 4315
9892 9928.848 9936 index: 4316
9888 9923.228 9928 index: 4317
9881 9914.508 9919 index: 4318
9845 9853.29 9866 index: 4322
9819 9820.325 9851 index: 4323
9793 9802.464 9828 index: 4324
9774 9788.914 9805 index: 4325
9735 9754.83 9761 index: 4329
9719 9730.981 9747 index: 4330
9696 9703.123 9729 index: 4331
9601 9611.284 9635 index: 4334
9578 9605.243 9606 index: 4335
9551 9567.358 9578 index: 4338
9380 9380.308 9402 index: 4344
9355 9368.858 9379 index: 4345
9337 9351.815 9364 index: 4346
9319 9331.369 9349 index: 4347
9298 9300.409 9329 index: 4348
255 2

36990 36998.043 36999 index: 35555
36691 36698.992 36699 index: 35561
36490 36496.79 36500 index: 35565
36438 36446.36 36448 index: 35566
36389 36398.617 36399 index: 35567
36240 36246.85 36248 index: 35570
36091 36097.48 36099 index: 35573
35989 35996.22 35999 index: 35575
35938 35945.094 35947 index: 35576
35889 35897.36 35898 index: 35577
35792 35798.42 35799 index: 35579
35741 35746.598 35748 index: 35580
35690 35697.17 35698 index: 35581
35590 35597.914 35599 index: 35583
35541 35546.086 35549 index: 35584
35491 35493.26 35498 index: 35585
35438 35442.832 35448 index: 35586
35389 35395.094 35398 index: 35587
35340 35345.977 35348 index: 35588
35240 35243.625 35249 index: 35590
35189 35193.203 35198 index: 35591
35139 35147.18 35148 index: 35592
35090 35097.35 35099 index: 35593
35041 35046.53 35049 index: 35594
34991 34991.29 34999 index: 35595
34939 34943.266 34949 index: 35596
34889 34896.54 34899 index: 35597
34840 34848.426 34850 index: 35598
34792 34796.9 34800 index: 35599
3

In [226]:
for i in range(n-2):
    print(min_kord[i], test_predict_0[i][0], max_kord[i], 'index:', i)

-1 -0.43621117 0 index: 0
-1 -0.43621117 0 index: 1
-1 2.4774337 1 index: 2
0 11.052605 5 index: 3
2 20.567179 12 index: 4
7 27.542511 21 index: 5
14 30.893227 31 index: 6
20 38.39985 38 index: 7
25 37.442535 36 index: 8
26 33.171307 39 index: 9
29 36.70125 39 index: 10
34 41.247803 43 index: 11
40 49.578728 54 index: 12
45 64.3153 67 index: 13
54 82.79783 74 index: 14
60 99.95979 95 index: 15
69 108.26947 108 index: 16
82 107.06806 111 index: 17
91 112.810295 113 index: 18
104 123.06485 119 index: 19
115 138.26611 135 index: 20
124 155.75027 146 index: 21
133 180.60326 158 index: 22
150 213.892 181 index: 23
181 241.22095 207 index: 24
209 239.0313 231 index: 25
227 248.07312 240 index: 26
237 246.70839 251 index: 27
241 254.82587 255 index: 28
246 282.1384 262 index: 29
257 314.37314 280 index: 30
277 340.45758 306 index: 31
307 370.06073 327 index: 32
340 405.20337 354 index: 33
375 431.94406 389 index: 34
403 427.21075 419 index: 35
414 440.77753 430 index: 36
419 449.23718 441 ind

169994 170428.38 170002 index: 12021
169994 170428.38 170002 index: 12022
169994 170428.38 170002 index: 12023
169994 170428.38 170002 index: 12024
169994 170428.38 170002 index: 12025
169994 170428.38 170002 index: 12026
169994 170428.38 170002 index: 12027
169994 170428.38 170002 index: 12028
169994 170428.38 170002 index: 12029
169994 170428.39 170002 index: 12030
169994 170428.39 170002 index: 12031
169994 170428.38 170002 index: 12032
169994 170428.38 170002 index: 12033
169994 170428.38 170002 index: 12034
169994 170428.38 170002 index: 12035
169994 170428.38 170002 index: 12036
169994 170428.38 170002 index: 12037
169994 170428.38 170002 index: 12038
169994 170428.38 170002 index: 12039
169994 170428.38 170002 index: 12040
169994 170428.38 170002 index: 12041
169994 170428.38 170002 index: 12042
169994 170428.38 170002 index: 12043
169994 170428.38 170002 index: 12044
169994 170428.38 170002 index: 12045
169994 170428.38 170002 index: 12046
169994 170428.38 170002 index: 12047
1

88749 89061.31 88757 index: 24720
88800 89113.14 88807 index: 24721
88850 89162.58 88858 index: 24722
88900 89210.984 88907 index: 24723
88948 89261.83 88957 index: 24724
88999 89311.95 89008 index: 24725
89049 89362.06 89060 index: 24726
89100 89412.17 89110 index: 24727
89149 89462.31 89158 index: 24728
89199 89512.46 89207 index: 24729
89248 89562.586 89257 index: 24730
89299 89616.09 89307 index: 24731
89350 89664.836 89358 index: 24732
89400 89713.234 89407 index: 24733
89451 89764.09 89457 index: 24734
89499 89814.2 89509 index: 24735
89549 89866.04 89559 index: 24736
89600 89915.47 89610 index: 24737
89650 89963.91 89659 index: 24738
89700 90014.7 89708 index: 24739
89749 90064.86 89757 index: 24740
89799 90114.95 89807 index: 24741
89850 90165.08 89858 index: 24742
89900 90213.52 89906 index: 24743
89949 90262.64 89956 index: 24744
89999 90315.17 90007 index: 24745
90049 90364.586 90058 index: 24746
90099 90413.016 90109 index: 24747
90148 90463.85 90158 index: 24748
90199 9051

37995 38096.08 38004 index: 37501
37995 38096.07 38004 index: 37502
37995 38096.07 38004 index: 37503
37995 38096.08 38004 index: 37504
37995 38096.08 38004 index: 37505
37995 38096.08 38004 index: 37506
37995 38096.08 38004 index: 37507
37995 38096.08 38004 index: 37508
37995 38096.08 38004 index: 37509
37995 38096.08 38004 index: 37510
37995 38096.08 38004 index: 37511
37995 38096.08 38003 index: 37512
37989 38090.97 38001 index: 37513
37978 38081.156 38000 index: 37514
37968 38069.035 37998 index: 37515
37963 38060.707 37992 index: 37516
37963 38063.598 37983 index: 37517
37963 38066.688 37978 index: 37518
37960 38064.29 37975 index: 37519
37956 38059.887 37970 index: 37520
37946 38046.67 37969 index: 37521
37936 38034.246 37968 index: 37522
37929 38026.625 37962 index: 37523
37917 38014.2 37950 index: 37524
37905 38004.867 37939 index: 37525
37895 37998.246 37933 index: 37526
37884 37988.52 37926 index: 37527
37872 37974.402 37914 index: 37528
37865 37960.668 37898 index: 37529
378

179994 180453.64 180004 index: 50292
179994 180453.64 180004 index: 50293
179994 180453.64 180004 index: 50294
179994 180457.05 180004 index: 50295
179995 180455.67 180005 index: 50296
179995 180453.95 180006 index: 50297
179994 180452.94 180005 index: 50298
179994 180453.64 180004 index: 50299
179993 180453.64 180004 index: 50300
179994 180453.64 180003 index: 50301
179994 180453.64 180004 index: 50302
179994 180453.64 180004 index: 50303
179994 180453.64 180004 index: 50304
179994 180457.05 180004 index: 50305
179994 180455.67 180005 index: 50306
179995 180453.95 180006 index: 50307
179994 180452.94 180005 index: 50308
179994 180453.64 180004 index: 50309
179993 180453.64 180004 index: 50310
179994 180453.64 180003 index: 50311
179994 180453.64 180004 index: 50312
179994 180453.64 180004 index: 50313
179994 180455.36 180004 index: 50314
179994 180454.64 180004 index: 50315
179995 180456.36 180006 index: 50316
179995 180455.67 180006 index: 50317
179994 180452.27 180005 index: 50318
1

In [227]:
avg = [0 for x in range(n)]
for i in range(n-2):
    for j in range(duzina):
        exec(f"avg[i] += test_predict_{j}[i][0]")
    avg[i] = avg[i]/15
    print(min_kord[i],avg[i],max_kord[i], 'index:',i)

-1 -0.46988896081844966 0 index: 0
-1 0.20788288190960885 0 index: 1
-1 6.249379931886991 1 index: 2
0 12.898782126108806 5 index: 3
2 21.63312110900879 12 index: 4
7 29.224667358398438 21 index: 5
14 36.356329600016274 31 index: 6
20 35.8144723256429 38 index: 7
25 38.79084726969401 36 index: 8
26 39.89118372599284 39 index: 9
29 45.28340555826823 39 index: 10
34 52.5717658996582 43 index: 11
40 61.9657595316569 54 index: 12
45 72.18126856486002 67 index: 13
54 80.10184733072917 74 index: 14
60 91.90200398763021 95 index: 15
69 102.61024525960286 108 index: 16
82 109.72563883463542 111 index: 17
91 119.50447235107421 113 index: 18
104 129.50098571777343 119 index: 19
115 141.5338612874349 135 index: 20
124 150.00127970377605 146 index: 21
133 172.6517303466797 158 index: 22
150 203.6143768310547 181 index: 23
181 232.2825897216797 207 index: 24
209 240.13184407552083 231 index: 25
227 247.55521647135416 240 index: 26
237 248.7569590250651 251 index: 27
241 254.83747049967448 255 index

9994 10003.862369791666 10003 index: 459
9994 10003.862369791666 10003 index: 460
9994 10003.862369791666 10003 index: 461
9994 10003.862369791666 10003 index: 462
9994 10003.862369791666 10003 index: 463
9994 10003.862369791666 10003 index: 464
9994 10003.862369791666 10003 index: 465
9994 10003.862369791666 10003 index: 466
9994 10003.862369791666 10003 index: 467
9994 10003.862369791666 10003 index: 468
9994 10003.862369791666 10003 index: 469
9994 10003.862369791666 10003 index: 470
9994 10003.862369791666 10003 index: 471
9994 10003.862369791666 10003 index: 472
9994 10003.862369791666 10003 index: 473
9994 10003.783919270832 10003 index: 474
9993 10003.795638020832 10003 index: 475
9993 10003.795638020832 10003 index: 476
9993 10003.987434895833 10003 index: 477
9994 10003.968294270833 10003 index: 478
9994 10003.9958984375 10003 index: 479
9994 10003.956705729166 10003 index: 480
9994 10003.737239583334 10003 index: 481
9993 10003.6990234375 10003 index: 482
9993 10003.662109375

9995 10003.996028645834 10003 index: 927
9995 10003.995703125 10003 index: 928
9995 10003.995703125 10003 index: 929
9995 10003.995703125 10003 index: 930
9995 10003.995703125 10003 index: 931
9995 10003.995703125 10003 index: 932
9995 10003.995703125 10003 index: 933
9995 10003.995703125 10003 index: 934
9995 10003.995703125 10003 index: 935
9995 10003.995703125 10003 index: 936
9995 10003.995703125 10003 index: 937
9995 10003.995703125 10003 index: 938
9995 10003.995703125 10003 index: 939
9995 10003.995703125 10003 index: 940
9995 10003.995703125 10003 index: 941
9995 10003.995703125 10003 index: 942
9995 10003.995703125 10003 index: 943
9995 10003.995703125 10003 index: 944
9995 10003.995703125 10003 index: 945
9995 10003.995703125 10003 index: 946
9995 10003.995703125 10003 index: 947
9995 10003.995703125 10003 index: 948
9995 10003.995703125 10003 index: 949
9995 10003.995703125 10003 index: 950
9995 10003.995703125 10003 index: 951
9995 10003.995703125 10003 index: 952
9995 1000

9995 10003.995703125 10003 index: 1399
9995 10003.995703125 10003 index: 1400
9995 10003.995703125 10003 index: 1401
9995 10003.995703125 10003 index: 1402
9995 10004.053059895834 10003 index: 1403
9995 10004.062434895834 10003 index: 1404
9995 10004.062434895834 10003 index: 1405
9995 10004.0626953125 10003 index: 1406
9995 10004.0626953125 10003 index: 1407
9995 10004.062434895834 10003 index: 1408
9995 10004.062434895834 10003 index: 1409
9995 10004.062434895834 10003 index: 1410
9995 10004.062434895834 10003 index: 1411
9995 10004.062434895834 10003 index: 1412
9995 10004.062434895834 10003 index: 1413
9995 10004.062434895834 10003 index: 1414
9995 10004.062434895834 10003 index: 1415
9995 10004.062434895834 10003 index: 1416
9995 10004.062434895834 10003 index: 1417
9995 10004.062434895834 10003 index: 1418
9995 10004.062434895834 10003 index: 1419
9995 10004.062434895834 10003 index: 1420
9995 10004.062434895834 10003 index: 1421
9995 10004.062434895834 10003 index: 1422
9995 100

9995 10003.995703125 10003 index: 1858
9995 10003.995703125 10003 index: 1859
9995 10003.995703125 10003 index: 1860
9995 10003.995703125 10003 index: 1861
9995 10003.995703125 10003 index: 1862
9995 10003.995703125 10003 index: 1863
9995 10003.995703125 10003 index: 1864
9995 10003.995703125 10003 index: 1865
9995 10003.995703125 10003 index: 1866
9995 10003.995703125 10003 index: 1867
9995 10003.995703125 10003 index: 1868
9995 10003.995703125 10003 index: 1869
9995 10003.995703125 10003 index: 1870
9995 10003.995703125 10003 index: 1871
9995 10003.995703125 10003 index: 1872
9995 10003.995703125 10003 index: 1873
9995 10003.995703125 10003 index: 1874
9995 10003.995703125 10003 index: 1875
9995 10003.995703125 10003 index: 1876
9995 10003.995703125 10003 index: 1877
9995 10003.995703125 10003 index: 1878
9995 10003.995703125 10003 index: 1879
9995 10003.995703125 10003 index: 1880
9995 10003.995703125 10003 index: 1881
9995 10003.995703125 10003 index: 1882
9995 10003.995703125 1000

...

54140 54114.64609375 54149 index: 58692
54092 54066.341145833336 54099 index: 58693
54043 54016.751302083336 54051 index: 58694
53993 53964.46953125 54000 index: 58695
53939 53913.43072916667 53949 index: 58696
53888 53864.58932291667 53900 index: 58697
53840 53816.95 53851 index: 58698
53794 53768.0953125 53801 index: 58699
53744 53716.484635416666 53751 index: 58700
53691 53664.87578125 53700 index: 58701
53641 53615.28411458333 53650 index: 58702
53592 53566.22421875 53601 index: 58703
53543 53516.8484375 53551 index: 58704
53493 53465.99401041667 53500 index: 58705
53441 53415.57708333333 53449 index: 58706
53391 53366.37265625 53400 index: 58707
53343 53315.87317708333 53351 index: 58708
53293 53265.990885416664 53301 index: 58709
53241 53215.20364583333 53249 index: 58710
53191 53164.61223958333 53198 index: 58711
53141 53115.50572916667 53149 index: 58712
53093 53066.309895833336 53100 index: 58713
53044 53016.18515625 53050 index: 58714
52992 52965.11015625 53000 index: 58715
5

30743 30711.681380208334 30749 index: 59160
30691 30660.651953125 30699 index: 59161
30642 30610.582682291668 30650 index: 59162
30592 30561.025651041666 30601 index: 59163
30542 30511.668880208334 30550 index: 59164
30491 30460.657291666666 30499 index: 59165
30440 30410.05 30449 index: 59166
30390 30360.255598958334 30399 index: 59167
30342 30310.473046875 30349 index: 59168
30292 30260.406380208333 30299 index: 59169
30241 30209.595963541666 30247 index: 59170
30191 30159.226302083334 30198 index: 59171
30141 30110.449479166666 30148 index: 59172
30093 30060.8359375 30099 index: 59173
30043 30010.91328125 30049 index: 59174
29992 29959.39375 29998 index: 59175
29941 29908.847526041667 29949 index: 59176
29890 29859.640104166665 29899 index: 59177
29841 29810.6921875 29850 index: 59178
29793 29761.659505208332 29799 index: 59179
29743 29710.909895833334 29749 index: 59180
29692 29660.0328125 29698 index: 59181
29642 29609.93046875 29649 index: 59182
29591 29560.363151041667 29600 ind

6642 6606.48740234375 6650 index: 59642
6591 6556.868294270834 6601 index: 59643
6542 6507.16494140625 6550 index: 59644
6492 6456.334765625 6500 index: 59645
6441 6405.717610677083 6450 index: 59646
6390 6355.82646484375 6400 index: 59647
6340 6305.76875 6350 index: 59648
6291 6255.593326822916 6299 index: 59649
6241 6204.728059895833 6249 index: 59650
6189 6154.588802083334 6199 index: 59651
6139 6105.88408203125 6149 index: 59652
6091 6055.88984375 6100 index: 59653
6040 6005.81650390625 6049 index: 59654
5990 5954.722233072916 5999 index: 59655
5939 5903.968424479167 5949 index: 59656
5889 5854.524739583333 5899 index: 59657
5840 5805.568196614583 5850 index: 59658
5791 5756.377669270833 5799 index: 59659
5741 5705.647819010416 5749 index: 59660
5690 5655.105859375 5699 index: 59661
5640 5605.419791666666 5649 index: 59662
5591 5555.384895833334 5599 index: 59663
5541 5505.436979166667 5549 index: 59664
5491 5454.66787109375 5499 index: 59665
5439 5404.24482421875 5448 index: 59666

-6 -2.789121658106645 1 index: 60105
-6 -2.789121658106645 1 index: 60106
-6 -2.789121658106645 1 index: 60107
-6 -2.789121658106645 1 index: 60108
-6 -2.789121658106645 1 index: 60109
-6 -2.789121658106645 1 index: 60110
-6 -2.789121658106645 1 index: 60111
-6 -2.789121658106645 1 index: 60112
-6 -2.789121658106645 1 index: 60113
-6 -2.789121658106645 1 index: 60114
-6 -2.789121658106645 1 index: 60115
-6 -2.789121658106645 1 index: 60116
-6 -2.789121658106645 1 index: 60117
-6 -2.789121658106645 1 index: 60118
-6 -2.789121658106645 1 index: 60119
-6 -2.789121658106645 1 index: 60120
-6 -2.789121658106645 1 index: 60121
-6 -2.789121658106645 1 index: 60122
-6 -2.789121658106645 1 index: 60123
-6 -2.789121658106645 1 index: 60124
-6 -2.789121658106645 1 index: 60125
-6 -2.7891215992470584 1 index: 60126
-6 -2.7891215992470584 1 index: 60127
-6 -2.789121658106645 1 index: 60128
-6 -2.789121658106645 1 index: 60129
-6 -2.789121658106645 1 index: 60130
-6 -2.789121658106645 1 index: 60131

-6 -2.6544566810131074 1 index: 60574
-6 -2.6544566810131074 1 index: 60575
-6 -2.6544568320115407 1 index: 60576
-6 -2.6544568320115407 1 index: 60577
-6 -2.6544568320115407 1 index: 60578
-6 -2.6544568320115407 1 index: 60579
-6 -2.6544568320115407 1 index: 60580
-6 -2.6544568320115407 1 index: 60581
-6 -2.6544568320115407 1 index: 60582
-6 -2.6544568320115407 1 index: 60583
-6 -2.7476231515407563 1 index: 60584
-6 -2.7148131310939787 1 index: 60585
-6 -2.7148131310939787 1 index: 60586
-6 -2.7148131310939787 1 index: 60587
-6 -2.7148131310939787 1 index: 60588
-6 -2.7148131310939787 1 index: 60589
-6 -2.6298544426759083 1 index: 60590
-6 -2.6544568320115407 1 index: 60591
-6 -2.6544568320115407 1 index: 60592
-6 -2.6544568320115407 1 index: 60593
-6 -2.6544568320115407 1 index: 60594
-6 -2.6544568320115407 1 index: 60595
-6 -2.6544568320115407 1 index: 60596
-6 -2.6544568320115407 1 index: 60597
-6 -2.6544568320115407 1 index: 60598
-6 -2.6544568320115407 1 index: 60599
-6 -2.654456